# "Density" statistics & density plot

Statistics "density" are calculated on the sample of a single continuous variable.
It approximates the Probability Density Function (PDF) of this sample.
"Density" statistic samples this function point.
It's weighted, it means the counted density depends on observation weights.

This notebook uses definitions from [DataFrame](https://kotlin.github.io/dataframe/overview.html).

## Usage

"Density" statistic is useful when you have a large dataset,
and you want to understand the underlying probability distribution.
Density plot visualizes the PDF and also allows you to compare the distribution of different samples.
This is a useful alternative to the histogram for continuous data that comes from an underlying smooth distribution.

## Arguments

* Input (mandatory):
    - `x` — numeric sample on which the statistics are calculated
* Weights (optional):
    - `weights` — set of weights of the same size as the input sample.
      `null` (by default) means all weights are equal to `1.0` and the weighted density is equal to the normal one
* Parameters (optional):
    - `n: Int` — number of sampled points;
    - `trim: Boolean` — if `false`, each density is computed on the full range of the data,
      if `true`, each density is computed over the range of that group (only for grouped inputs).
    - `adjust: Double` — adjusts the value of bandwidth by multiplying it; changes how smooth the frequency curve is.
    - `kernel: Kernel` — the kernel used to calculate the density function:
        - `Kernel.GAUSSIAN`
        - `Kernel.RECTANGULAR`
        - `Kernel.TRIANGULAR`
        - `Kernel.BIWEIGHT`
        - `Kernel.EPANECHNIKOV`
        - `Kernel.OPTCOSINE`
    - `fullScanMax: Int` — maximum size of data to use density computation with 'full scan'.
      For bigger data, less accurate but more efficient density computation is applied
    - `bandWidth: BandWidth` — the method (or exact value) of bandwidth:
        - `BandWidth.Method.NRD`
        - `BandWidth.Method.NRD0`
        - `BandWidth.value(value: Double)`

### Generalized signature

The specific signature depends on the function,
but all functions related to "density"
statistic (which will be discussed further below — different variations of `statDensity()`, `densityPlot()`)
have approximately the same signature with the arguments above:

```
statDensityArgs := 
   x, 
   weights = null,
   n: Int = 512,
   trim: Boolean = false,
   adjust: Double = 1.0,
   kernel: Kernel = Kernel.GAUSSIAN,
   fullScanMax: Int = 5000,
   bandWidth: BandWidth = BandWidth.Method.NRD0,
```

The possible types of `x` and `weights` depend on where a certain function is used.
They can be simply `Iterable` (`List`, `Set`, etc.) or a reference to a column in a `DataFrame`
(`String`, `ColumnAccessor`) or the `DataColumn` itself.

## Output statistics

| name                 | type   | description                                 |
|----------------------|--------|---------------------------------------------|
| Stat.x               | Double | `x` coordinate                              |
| Stat.density         | Double | Density estimate                            |
| Stat.densityWeighted | Double | Weighted density                            |
| Stat.scaled          | Double | Density estimate, scaled to maximin of 1.0. |
| Stat.scaledWeighted  | Double | Weighted scaled                             |

## StatDensity plots

In [1]:
%use dataframe
%use kandy

import org.apache.commons.math3.distribution.NormalDistribution
import org.apache.commons.math3.distribution.UniformRealDistribution
import org.jetbrains.kotlinx.statistics.dataframe.stat.mean

In [2]:
// To generate the data, we use a standard java math library
// https://commons.apache.org/proper/commons-math/
// Generate sample from normal distribution
val depthList = NormalDistribution(500.0, 100.0).sample(1000).toList()
// Generate sample from uniform distribution
val coeffList = UniformRealDistribution(0.0, 1.0).sample(1000).toList()

In [3]:
// Gather them into the DataFrame
val df = dataFrameOf(
    "depth" to depthList,
    "coeff" to coeffList
)
df.head()

<iframe onload="o_resize_iframe_out_1()" style="width:100%;" class="result_container" id="iframe_out_1" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-687865856"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for 

`df` has a signature

| depth | coeff |
|-------|-------|

Let's take a look at `StatDensity` output DataFrame:

In [4]:
df.statDensity("depth", "coeff").head(5)

<iframe onload="o_resize_iframe_out_2()" style="width:100%;" class="result_container" id="iframe_out_2" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-687865855"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 1</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for 

It has the following signature:

<table>
  <thead>
    <tr>
      <th alignt="left" colspan="5">Stat</th>
    </tr>
  </thead>
  <thead>
    <tr>
      <th>x</th>
      <th>density</th>
      <th>densityWeighted</th>
      <th>scaled</th>
      <th>scaledWeighted</th>
    </tr>
  </thead>
</table>

As you can see, we got a `DataFrame` with one `ColumnGroup` called `Stat` which contains several columns with statics.
For `statDensity`, each row corresponds to one PDF point.
`Stat.x` is the column with this point `x` coordinate.
`Stat.density` contains the estimated density.
`Stat.densityWeighted` — weighted version of `density`.
`Stat.scaled` is a density scaled to a maximum of 1.0.
`Stat.scaledWeighted` — weighted version of `scaled`.
`DataFrame` with "density" statistics is called `StatDensityFrame`

### `statDensity` transform

`statDensity(statDensityArgs) { /*new plotting context*/ }` modifies a plotting context —
instead of original data (no matter was it empty or not) new `StatDensity` dataset
(calculated on given arguments, inputs and weights can be provided as `Iterable` or as dataset column reference —
by name as a `String`, as a `ColumnReference` or as a `DataColumn`) is used inside a new context
(original dataset and primary context are not affected —
you can add layers using initial dataset outside the `statDensity` context).
Since the old dataset is irrelevant, we cannot use references for its columns.
But we can refer to the new ones.
They are all contained in the `Stat` group and can be called inside the new context:

In [5]:
plot {
    statDensity(depthList, adjust = 0.2) {
        // New `StatDensity` dataset here
        line {
            // Use `Stat.*` columns for mappings
            x(Stat.x)
            y(Stat.density)
            color(Stat.density)
        }
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="h6Tk3u"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"color",
"scale_mapper_kind":"color_gradient",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"color":"density"
},
"stat":"identity",
"data":{
"density":[8.904364879260682E-5,8.544026141296625E-5,7.548178362547075E-5,6.139704966491958E-5,4.598403573093709E-5,3.1722009958972075E-5,2.0188029439403308E-5,1.1943810977103215E-5,6.809448364225631E-6,4.306533134962124E-6,4.0646046856078825E-6,6.0721566659004315E-6,1.0733599571583749E-5,1.8736615573789175E-5,3.07654343906657E-5,4.714635344320338E-5,6.756923929351526E-5,9.103079977032053E-5,1.1604049710711854E-4,1.4095549283432365E-4,1.6420363788397207E-4,1.8424300233802957E-4,1.9936752593870214E-4,2.0768993572705023E-4,2.0758168574453966E-4,1.985008150409448E-4,1.8174260838690383E-4,1.6053773781936473E-4,1.392291062848985E-4,1.2179577204853132E-4,1.1040497973688852E-4,1.0470011215713399E-4,1.0216657717694298E-4,9.937977262802327E-5,9.352740730617598E-5,8.352358947100652E-5,7.031091112397497E-5,5.639509391604931E-5,4.4999739736444924E-5,3.927721582495959E-5,4.178727299538557E-5,5.416518065345998E-5,7.678000807927607E-5,1.0831755637999322E-4,1.4548772005888524E-4,1.8321207609016713E-4,2.1552184999037028E-4,2.3702937695656387E-4,2.444650731450074E-4,2.3765305620282052E-4,2.1951125271964722E-4,1.950665519297332E-4,1.6984944841292275E-4,1.4823180974080072E-4,1.3227000264373664E-4,1.2143811931478196E-4,1.1331594953384751E-4,1.0491739906756611E-4,9.407358243934467E-5,8.029017153700608E-5,6.48048392789208E-5,4.999663493958469E-5,3.857525378942546E-5,3.294955142045147E-5,3.491166675932123E-5,4.550086237574437E-5,6.483134782123784E-5,9.181845371633721E-5,1.2397778169629585E-4,1.5759186626815817E-4,1.8841086295532096E-4,2.1273730480650386E-4,2.284606769571204E-4,2.3557758877466135E-4,2.3599973788005738E-4,2.3283150559283422E-4,2.295279046465942E-4,2.2928651053311837E-4,2.3476671878792184E-4,2.4797500926073974E-4,2.700747615900043E-4,3.010032462751138E-4,3.390082827103613E-4,3.80401498980153E-4,4.1984353977101633E-4,4.5129775864238727E-4,4.6948581318682285E-4,4.7139447141385097E-4,4.5726737649820053E-4,4.30653871616311E-4,3.974452247369725E-4,3.6424675955098367E-4,3.3670119866422793E-4,3.18360040572922E-4,3.104241554826997E-4,3.12297512922334E-4,3.225889690352963E-4,3.400605317888901E-4,3.6409230166483764E-4,3.94496252496876E-4,4.308703784563664E-4,4.7196661580255694E-4,5.155734784000971E-4,5.591397435421177E-4,6.009234819116036E-4,6.410760537620374E-4,6.819649570609769E-4,7.272905716378383E-4,7.801056951934589E-4,8.404875863497674E-4,9.039975605613429E-4,9.618955242391865E-4,0.001003347389680572,0.0010189368877523532,0.0010041874405251902,9.618146185363427E-4,9.019618897940573E-4,8.403680242638806E-4,7.949758703416339E-4,7.818323867274919E-4,8.112849197823945E-4,8.854557029218646E-4,9.97730034694709E-4,0.0011345169163794223,0.0012789237157457467,0.0014153850928730856,0.0015338871224797183,0.001632430031684431,0.0017168997697322608,0.0017984348754386697,0.0018892395054705227,0.001998143917524716,0.0021269884890181452,0.002268509920453411,0.002406249522208038,0.0025170046827351984,0.002576009137462884,0.002564048579839793,0.0024744529804307846,0.0023172022214290092,0.0021179315798209464,0.0019114419809123792,0.0017316739400559614,0.0016018609421897,0.0015287615711382988,0.0015032095479885592,0.0015064146013988844,0.0015188901750524438,0.0015279198053019098,0.00153059501389866,0.0015319815307699859,0.0015404296326943432,0.0015630705862244958,0.0016037032665750129,0.001663313

### DensityPlot layer

Density plot is a statistical plot used for visualizing the distribution of continuous variables.
It's an area graph of kernel-estimated PDF.
So basically, we can build a histogram with `statDensity` as follows:

In [6]:
val statDensityAndAreaPlot = df.plot {
    statDensity("depth") {
        area {
            x(Stat.x)
            y(Stat.density)
        }
    }
    layout.title = "`statDensity()` + `area()` layer"
}
statDensityAndAreaPlot

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="07N0cu"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"ggtitle":{
"text":"`statDensity()` + `area()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[4.4745487622806146E-5,4.696816529975255E-5,4.9233293830303676E-5,5.153731555102641E-5,5.387633276816177E-5,5.624611129478038E-5,5.864209041236017E-5,6.105939982177893E-5,6.349288396567802E-5,6.593713389500998E-5,6.838652662506085E-5,7.083527168925842E-5,7.327746436241661E-5,7.570714479888997E-5,7.811836212549253E-5,8.050524235343432E-5,8.286205883632316E-5,8.518330390927977E-5,8.746376030227882E-5,8.969857093154006E-5,9.188330573629249E-5,9.401402434205878E-5,9.608733349085005E-5,9.810043837604224E-5,1.00051187245957E-4,1.0193810888445897E-4,1.0376044282723836E-4,1.0551816241653399E-4,1.0721199102260851E-4,1.0884341195590564E-4,1.1041467274953226E-4,1.1192878459951065E-4,1.1338951780461206E-4,1.1480139404582086E-4,1.1616967628787538E-4,1.1750035697532572E-4,1.1880014503949158E-4,1.2007645203972864E-4,1.213373775439211E-4,1.2259169362225652E-4,1.2384882809946094E-4,1.2511884599835198E-4,1.2641242842620088E-4,1.2774084801807153E-4,1.2911593996937963E-4,1.305500676721586E-4,1.3205608202175126E-4,1.3364727358514844E-4,1.3533731701773308E-4,1.3714020737666795E-4,1.3907018829802356E-4,1.4114167236907113E-4,1.4336915442223874E-4,1.4576711888616745E-4,1.4834994273368746E-4,1.5113179594735402E-4,1.5412654176153617E-4,1.5734763921820846E-4,1.6080805077558423E-4,1.6452015782133876E-4,1.6849568695538134E-4,1.7274564981478152E-4,1.7728029901348678E-4,1.821091024641407E-4,1.8724073794515873E-4,1.9268310928388516E-4,1.9844338496041402E-4,2.0452805931399834E-4,2.1094303587480825E-4,2.1769373166968087E-4,2.2478520068392014E-4,2.3222227402433531E-4,2.4000971374304837E-4,2.4815237676644E-4,2.5665538494609236E-4,2.6552429692217115E-4,2.7476527727442527E-4,2.8438525833768535E-4,2.943920900790142E-4,3.0479467356997415E-4,3.1560307383331736E-4,3.268286081887827E-4,3.3848390665449794E-4,3.5058294146366766E-4,3.6314102331389035E-4,3.7617476256143994E-4,3.8970199418804596E-4,4.0374166598730827E-4,4.183136900276523E-4,4.334387580374131E-4,4.491381219162523E-4,4.654333411006914E-4,4.8234599899770007E-4,4.99897391150355E-4,5.181081882170567E-4,5.36998077237055E-4,5.565853850268467E-4,5.768866879127005E-4,5.979164123608389E-4,6.196864314246854E-4,6.422056622908286E-4,6.65479670571771E-4,6.895102873594503E-4,7.142952454096919E-4,7.398278411604051E-4,7.660966295763934E-4,7.930851590385885E-4,8.207717536288285E-4,8.49129350174689E-4,8.781253972829936E-4,9.077218232774836E-4,9.378750794400418E-4,9.685362642152697E-4,9.996513330608216E-4,0.0010311613974048957,0.00106300311471148,0.0010951091699676631,0.0011274088470219288,0.0011598286861550066,0.0011922932221040702,0.0012247257945453543,0.0012570494208360408,0.0012891877186964123,0.0013210658645537916,0.00135261157154707,0.0013837560697783538,0.0014144350703638093,0.0014445896942369915,0.0014741673465403324,0.0015031225178347132,0.0015314174942760964,0.0015590229603474825,0.0015859184796696373,0.0016120928418024679,0.0016375442657296426,0.0016622804538162866,0.001686318493353416,0.001709684606253592,0.001732413750935259,0.001754549083820206,0.0017761412910652266,0.0017972478040555238,0.001817931914717397,0.0018382618087848725,0.0018583095367235754,0.0018781499430355448,0.0018978595751227485,0.0019175155927767251,0.0019371946987085911,0.0019569721093776306,0.0019769205837737807,0.0019971095258286475,0.0020176041738501384,0.0020384648878806807,0.002059746543257072,0.00208149803598309

But we can do it even faster with `densityPlot(statDensityArgs)` method:

In [7]:
val densityLayerPlot = plot {
    densityPlot(depthList)
    layout.title = "`densityPlot()` layer"
}
densityLayerPlot

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="s26mTj"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"ggtitle":{
"text":"`densityPlot()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"x",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[4.4745487622806146E-5,4.696816529975255E-5,4.9233293830303676E-5,5.153731555102641E-5,5.387633276816177E-5,5.624611129478038E-5,5.864209041236017E-5,6.105939982177893E-5,6.349288396567802E-5,6.593713389500998E-5,6.838652662506085E-5,7.083527168925842E-5,7.327746436241661E-5,7.570714479888997E-5,7.811836212549253E-5,8.050524235343432E-5,8.286205883632316E-5,8.518330390927977E-5,8.746376030227882E-5,8.969857093154006E-5,9.188330573629249E-5,9.401402434205878E-5,9.608733349085005E-5,9.810043837604224E-5,1.00051187245957E-4,1.0193810888445897E-4,1.0376044282723836E-4,1.0551816241653399E-4,1.0721199102260851E-4,1.0884341195590564E-4,1.1041467274953226E-4,1.1192878459951065E-4,1.1338951780461206E-4,1.1480139404582086E-4,1.1616967628787538E-4,1.1750035697532572E-4,1.1880014503949158E-4,1.2007645203972864E-4,1.213373775439211E-4,1.2259169362225652E-4,1.2384882809946094E-4,1.2511884599835198E-4,1.2641242842620088E-4,1.2774084801807153E-4,1.2911593996937963E-4,1.305500676721586E-4,1.3205608202175126E-4,1.3364727358514844E-4,1.3533731701773308E-4,1.3714020737666795E-4,1.3907018829802356E-4,1.4114167236907113E-4,1.4336915442223874E-4,1.4576711888616745E-4,1.4834994273368746E-4,1.5113179594735402E-4,1.5412654176153617E-4,1.5734763921820846E-4,1.6080805077558423E-4,1.6452015782133876E-4,1.6849568695538134E-4,1.7274564981478152E-4,1.7728029901348678E-4,1.821091024641407E-4,1.8724073794515873E-4,1.9268310928388516E-4,1.9844338496041402E-4,2.0452805931399834E-4,2.1094303587480825E-4,2.1769373166968087E-4,2.2478520068392014E-4,2.3222227402433531E-4,2.4000971374304837E-4,2.4815237676644E-4,2.5665538494609236E-4,2.6552429692217115E-4,2.7476527727442527E-4,2.8438525833768535E-4,2.943920900790142E-4,3.0479467356997415E-4,3.1560307383331736E-4,3.268286081887827E-4,3.3848390665449794E-4,3.5058294146366766E-4,3.6314102331389035E-4,3.7617476256143994E-4,3.8970199418804596E-4,4.0374166598730827E-4,4.183136900276523E-4,4.334387580374131E-4,4.491381219162523E-4,4.654333411006914E-4,4.8234599899770007E-4,4.99897391150355E-4,5.181081882170567E-4,5.36998077237055E-4,5.565853850268467E-4,5.768866879127005E-4,5.979164123608389E-4,6.196864314246854E-4,6.422056622908286E-4,6.65479670571771E-4,6.895102873594503E-4,7.142952454096919E-4,7.398278411604051E-4,7.660966295763934E-4,7.930851590385885E-4,8.207717536288285E-4,8.49129350174689E-4,8.781253972829936E-4,9.077218232774836E-4,9.378750794400418E-4,9.685362642152697E-4,9.996513330608216E-4,0.0010311613974048957,0.00106300311471148,0.0010951091699676631,0.0011274088470219288,0.0011598286861550066,0.0011922932221040702,0.0012247257945453543,0.0012570494208360408,0.0012891877186964123,0.0013210658645537916,0.00135261157154707,0.0013837560697783538,0.0014144350703638093,0.0014445896942369915,0.0014741673465403324,0.0015031225178347132,0.0015314174942760964,0.0015590229603474825,0.0015859184796696373,0.0016120928418024679,0.0016375442657296426,0.0016622804538162866,0.001686318493353416,0.001709684606253592,0.001732413750935259,0.001754549083820206,0.0017761412910652266,0.0017972478040555238,0.001817931914717397,0.0018382618087848725,0.0018583095367235754,0.0018781499430355448,0.0018978595751227485,0.0019175155927767251,0.0019371946987085911,0.0019569721093776306,0.0019769205837737807,0.0019971095258286475,0.0020176041738501384,0.00203846488788068

Let's compare them:

In [8]:
plotGrid(listOf(statDensityAndAreaPlot, densityLayerPlot))

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="Q5UhiM"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"layout":{
"name":"grid",
"ncol":2,
"nrow":1,
"fit":true,
"align":false
},
"figures":[{
"ggtitle":{
"text":"`statDensity()` + `area()` layer"
},
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[4.4745487622806146E-5,4.696816529975255E-5,4.9233293830303676E-5,5.153731555102641E-5,5.387633276816177E-5,5.624611129478038E-5,5.864209041236017E-5,6.105939982177893E-5,6.349288396567802E-5,6.593713389500998E-5,6.838652662506085E-5,7.083527168925842E-5,7.327746436241661E-5,7.570714479888997E-5,7.811836212549253E-5,8.050524235343432E-5,8.286205883632316E-5,8.518330390927977E-5,8.746376030227882E-5,8.969857093154006E-5,9.188330573629249E-5,9.401402434205878E-5,9.608733349085005E-5,9.810043837604224E-5,1.00051187245957E-4,1.0193810888445897E-4,1.0376044282723836E-4,1.0551816241653399E-4,1.0721199102260851E-4,1.0884341195590564E-4,1.1041467274953226E-4,1.1192878459951065E-4,1.1338951780461206E-4,1.1480139404582086E-4,1.1616967628787538E-4,1.1750035697532572E-4,1.1880014503949158E-4,1.2007645203972864E-4,1.213373775439211E-4,1.2259169362225652E-4,1.2384882809946094E-4,1.2511884599835198E-4,1.2641242842620088E-4,1.2774084801807153E-4,1.2911593996937963E-4,1.305500676721586E-4,1.3205608202175126E-4,1.3364727358514844E-4,1.3533731701773308E-4,1.3714020737666795E-4,1.3907018829802356E-4,1.4114167236907113E-4,1.4336915442223874E-4,1.4576711888616745E-4,1.4834994273368746E-4,1.5113179594735402E-4,1.5412654176153617E-4,1.5734763921820846E-4,1.6080805077558423E-4,1.6452015782133876E-4,1.6849568695538134E-4,1.7274564981478152E-4,1.7728029901348678E-4,1.821091024641407E-4,1.8724073794515873E-4,1.9268310928388516E-4,1.9844338496041402E-4,2.0452805931399834E-4,2.1094303587480825E-4,2.1769373166968087E-4,2.2478520068392014E-4,2.3222227402433531E-4,2.4000971374304837E-4,2.4815237676644E-4,2.5665538494609236E-4,2.6552429692217115E-4,2.7476527727442527E-4,2.8438525833768535E-4,2.943920900790142E-4,3.0479467356997415E-4,3.1560307383331736E-4,3.268286081887827E-4,3.3848390665449794E-4,3.5058294146366766E-4,3.6314102331389035E-4,3.7617476256143994E-4,3.8970199418804596E-4,4.0374166598730827E-4,4.183136900276523E-4,4.334387580374131E-4,4.491381219162523E-4,4.654333411006914E-4,4.8234599899770007E-4,4.99897391150355E-4,5.181081882170567E-4,5.36998077237055E-4,5.565853850268467E-4,5.768866879127005E-4,5.979164123608389E-4,6.196864314246854E-4,6.422056622908286E-4,6.65479670571771E-4,6.895102873594503E-4,7.142952454096919E-4,7.398278411604051E-4,7.660966295763934E-4,7.930851590385885E-4,8.207717536288285E-4,8.49129350174689E-4,8.781253972829936E-4,9.077218232774836E-4,9.378750794400418E-4,9.685362642152697E-4,9.996513330608216E-4,0.0010311613974048957,0.00106300311471148,0.0010951091699676631,0.0011274088470219288,0.0011598286861550066,0.0011922932221040702,0.0012247257945453543,0.0012570494208360408,0.0012891877186964123,0.0013210658645537916,0.00135261157154707,0.0013837560697783538,0.0014144350703638093,0.0014445896942369915,0.0014741673465403324,0.0015031225178347132,0.0015314174942760964,0.0015590229603474825,0.0015859184796696373,0.0016120928418024679,0.0016375442657296426,0.0016622804538162866,0.001686318493353416,0.001709684606253592,0.001732413750935259,0.001754549083820206,0.0017761412910652266,0.0017972478040555238,0.001817931914717397,0.0018382618087848725,0.0018583095367235754,0.0018781499430355448,0.0018978595751227485,0.0019175155927767251,0.0019371946987085911,0.0019569721093776306,0.0019769205837737807,0.0019971095258286

These two plots are identical.
Indeed, `densityPlot` just uses `statDensity` and `area` and performs coordinate mappings under the hood.
And we can customize `densityPlot` layer: `densityPlot()` optionally opens a new context,
where we can configure bars (as in the usual context opened by `area { ... }`) —
even change coordinate mappings from default ones.
`StatDensity` dataset of `densityPlot` is also can be accessed here.

In [9]:
df.plot {
    densityPlot(depth) {
        // Change a column mapped on `y` to `Stat.scaled`
        y(Stat.scaled)
        alpha = 0.7
        fillColor = Color.RED
        borderLine.color = Color.BLACK
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="kXEEMf"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"scaled"
},
"stat":"identity",
"data":{
"scaled":[0.011669694202816286,0.012249372069331936,0.01284012118585589,0.013441013708117212,0.014051033111396211,0.014669075113020182,0.015293950270358701,0.015924388401669386,0.016559044929408972,0.017196509191079484,0.01783531470334138,0.018473951303320604,0.019110879029315228,0.019744543544120023,0.020373392850561424,0.02099589500303841,0.02161055648308119,0.02221594088294615,0.022810687530328586,0.023393529690068283,0.0239633119952837,0.02451900679005604,0.02505972910731522,0.02558475005705708,0.02609350845902814,0.026585620617724827,0.027060888202847955,0.027519304262011098,0.027961057451327057,0.028386534620514214,0.028796321929774677,0.029191204703811147,0.029572166242528293,0.029940385807504733,0.03029723598829887,0.03064427962396201,0.03098326641443237,0.03131612930615531,0.03164498067929261,0.03197210830367432,0.03229997097095512,0.032631193655063444,0.032968562005731256,0.03331501594407787,0.033673642107855346,0.03404766488933215,0.03444043582241372,0.03485542110806925,0.03529618711813031,0.035766383785721265,0.03626972587374022,0.036809972207826634,0.037390903063287434,0.03801629600210537,0.03868990056161715,0.039415412295767165,0.040196446758085945,0.041036514088085854,0.04193899491544607,0.04290711832572703,0.04394394263480032,0.045052339695094035,0.04623498340460106,0.047494343009968604,0.04883268168958286,0.050252060774162076,0.05175434981469432,0.05334124254516613,0.05501427861561741,0.056774870795246464,0.058624337171443476,0.06056393770453338,0.06259491434526906,0.06471853378776071,0.06693613181903153,0.06924915814126081,0.07165922048663292,0.07416812681907638,0.07677792442246252,0.07949093471038468,0.08230978265675432,0.08523741983652482,0.08827714017847338,0.09143258766319978,0.09470775534494257,0.0981069752309859,0.10163489871287681,0.10529646740526466,0.10909687440720399,0.11304151615429146,0.117135935175695,0.12138575420668367,0.12579660223405756,0.13037403316925644,0.13512343795280468,0.14004995099579054,0.14515835196104918,0.15045296398078534,0.15593754950029104,0.1616152050307469,0.1674882561885707,0.17355815449433823,0.1798253774997335,0.18628933390387675,0.19294827540713314,0.19979921712615514,0.20683786845257385,0.2140585762725233,0.2214542824676741,0.22901649758301248,0.2367352924649336,0.24459930953862152,0.25259579520080006,0.26071065454903297,0.26892852935031214,0.2772328997706933,0.2856062099479505,0.2940300169975107,0.3024851625079752,0.31095196501900235,0.3194104313964604,0.3278404844448971,0.3362222035445099,0.3445360745887665,0.35276324504953877,0.3608857796282879,0.36888691168205534,0.37675128545684516,0.3844651841303125,0.39201673876849163,0.39939611354098903,0.4065956629144348,0.41361005704868287,0.42043637224316127,0.4270741440059834,0.433525381126201,0.4397945399964361,0.4458884593331103,0.45181625634724837,0.45758918630216106,0.4632204682280015,0.4687250803211994,0.47411952921660594,0.47942159786189587,0.48465007713288,0.48982448659450134,0.4949647899307075,0.5000911105376183,0.505223452604054,0.5103814327019974,0.5155840264915247,0.5208493346281734,0.5261943713662075,0.5316348787005103,0.5371851682060296,0.5428579920381723,0.5486644438715931,0.5546138898966506,0.5607139293783401,0.5669703837241457,0.5733873125142774,0.5799670545256953,0.5867102914325185,0.5936161315894175,0.6006822110983293,0.6079048092174918,0.6152789750895397,0.6227986627356463,0.6304568712792

If we specify weights, `Stat.densityWeighted` is mapped to `y` by default:

In [10]:
df.plot {
    densityPlot(depth, coeff, n = 700, adjust = 0.8, bandWidth = BandWidth.value(17.0))
    // We can add other layers as well.
    // Let's add a horizontal mark line with constant y intercept:
    vLine {
        // Count sample mean
        val mean = depth.mean()
        xIntercept.constant(mean)
        tooltips { line("Depth mean: ${String.format("%.2f", mean)}m") }
        color = Color.RED; width = 2.0
    }
    x.axis.name = "depth, m"
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="5NVdfo"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"x",
"name":"depth, m",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"densityWeighted"
},
"stat":"identity",
"data":{
"x":[185.72529353296983,186.66673687204812,187.60818021112644,188.54962355020473,189.49106688928305,190.43251022836134,191.37395356743963,192.31539690651795,193.25684024559624,194.19828358467456,195.13972692375285,196.08117026283117,197.02261360190946,197.96405694098775,198.90550028006606,199.84694361914435,200.78838695822267,201.72983029730096,202.67127363637925,203.61271697545757,204.55416031453586,205.49560365361418,206.43704699269247,207.37849033177076,208.31993367084908,209.26137700992737,210.2028203490057,211.14426368808398,212.0857070271623,213.0271503662406,213.96859370531888,214.9100370443972,215.8514803834755,216.79292372255378,217.7343670616321,218.6758104007104,219.6172537397887,220.558697078867,221.50014041794532,222.4415837570236,223.3830270961019,224.32447043518022,225.2659137742585,226.20735711333683,227.14880045241512,228.09024379149344,229.03168713057173,229.97313046965002,230.91457380872833,231.85601714780663,232.79746048688492,233.73890382596323,234.68034716504152,235.62179050411984,236.56323384319813,237.50467718227645,238.44612052135474,239.38756386043303,240.32900719951135,241.27045053858964,242.21189387766793,243.15333721674625,244.09478055582457,245.03622389490286,245.97766723398115,246.91911057305947,247.86055391213776,248.80199725121605,249.74344059029437,250.6848839293727,251.62632726845095,252.56777060752927,253.5092139466076,254.45065728568588,255.39210062476417,256.3335439638425,257.27498730292075,258.21643064199907,259.1578739810774,260.0993173201557,261.040760659234,261.9822039983123,262.9236473373906,263.86509067646887,264.8065340155472,265.7479773546255,266.6894206937038,267.6308640327821,268.5723073718604,269.5137507109387,270.455194050017,271.3966373890953,272.3380807281736,273.27952406725194,274.2209674063302,275.1624107454085,276.10385408448684,277.0452974235651,277.9867407626434,278.92818410172174,279.86962744080006,280.8110707798783,281.75251411895664,282.6939574580349,283.6354007971132,284.57684413619154,285.51828747526986,286.4597308143482,287.40117415342644,288.34261749250476,289.284060831583,290.22550417066134,291.16694750973966,292.108390848818,293.0498341878963,293.99127752697456,294.9327208660529,295.87416420513114,296.81560754420946,297.7570508832878,298.6984942223661,299.63993756144436,300.5813809005227,301.522824239601,302.46426757867926,303.4057109177576,304.3471542568359,305.2885975959142,306.2300409349925,307.1714842740708,308.1129276131491,309.0543709522274,309.9958142913057,310.937257630384,311.87870096946233,312.8201443085406,313.7615876476189,314.7030309866972,315.6444743257755,316.5859176648538,317.5273610039321,318.46880434301045,319.4102476820887,320.351691021167,321.2931343602453,322.2345776993236,323.1760210384019,324.11746437748025,325.05890771655856,326.0003510556368,326.94179439471515,327.8832377337934,328.8246810728717,329.76612441195005,330.70756775102836,331.6490110901067,332.59045442918494,333.5318977682632,334.4733411073415,335.41478444641984,336.35622778549816,337.2976711245765,338.23911446365474,339.18055780273306,340.1220011418113,341.06344448088964,342.00488781996796,342.9463311590463,343.8877744981246,344.82921783720286,345.7706611762812,346.71210451535944,347.65354785443776,348.5949911935161,349.5364345325944,350.4778778716727,351.419321210751,352.3607645498293,35

### `densityPlot` plot

`densityPlot(statDensityArgs)` and `DataFrame.densityPlot(statDensityArgs)`
are a family of functions for fast plotting a density plot.

In [11]:
densityPlot(depthList, kernel = Kernel.COSINE)

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="OQAmx9"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"x",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[4.463985557052566E-5,4.4276837498327444E-5,4.3206845752861475E-5,4.191551928108364E-5,4.071281167199456E-5,3.963784532794885E-5,3.872558740597736E-5,3.819863853949171E-5,3.858043149692059E-5,4.0205566309223804E-5,4.342566134534549E-5,4.8137324716227495E-5,5.418729257888627E-5,6.137876791036581E-5,6.947782204062647E-5,7.822100402616343E-5,8.732391034203643E-5,9.682649042172864E-5,1.0667603409359917E-4,1.1601649638349271E-4,1.244872483115185E-4,1.3181274812283203E-4,1.3775470751784926E-4,1.421198428385396E-4,1.4476616231644853E-4,1.4560758486703741E-4,1.4461674018739507E-4,1.418258590740466E-4,1.3732572500006152E-4,1.3126272105519593E-4,1.241102497440945E-4,1.1702405965501881E-4,1.1048745686384924E-4,1.0472788000785043E-4,1.0041234986189855E-4,9.791279892669381E-5,9.731053411062666E-5,9.858031913157098E-5,1.0115279208721478E-4,1.0479112255554664E-4,1.0942799936141604E-4,1.1544533285710618E-4,1.2246989827769493E-4,1.2986022525808717E-4,1.3691975514372231E-4,1.431556569365152E-4,1.483650854418918E-4,1.523785852107601E-4,1.5506560268910524E-4,1.5633873294315341E-4,1.5615656282005514E-4,1.5451426747882638E-4,1.5099915831374126E-4,1.4547666450562562E-4,1.385083823939159E-4,1.306999982014075E-4,1.228237723783201E-4,1.1530847728109514E-4,1.083985749854565E-4,1.0249114175271843E-4,9.829674660097028E-5,9.598714828560919E-5,9.563747482103215E-5,9.753214265575184E-5,1.020546222229498E-4,1.086034131658421E-4,1.1611200082029494E-4,1.2458788571487585E-4,1.344327443161571E-4,1.4511287453760062E-4,1.56433852954528E-4,1.6918615682052612E-4,1.8361189199635257E-4,1.9936038746885124E-4,2.1643743201109778E-4,2.3433629183140466E-4,2.5193811270709734E-4,2.6902421403961706E-4,2.853457302068899E-4,3.0037174503468847E-4,3.139242285588106E-4,3.2603061048742054E-4,3.368343394327094E-4,3.461197866269715E-4,3.5358590516815274E-4,3.5941766203937374E-4,3.6426115304368553E-4,3.6831971320846E-4,3.7209058408079284E-4,3.7555284726785226E-4,3.79172215728585E-4,3.82954903593372E-4,3.872371007473217E-4,3.920540293562943E-4,3.9754847277955336E-4,4.0430447181600345E-4,4.1364749503147567E-4,4.2635695690511723E-4,4.429803075444099E-4,4.639524426151499E-4,4.892017461333416E-4,5.187976196390101E-4,5.519454462322954E-4,5.869392678342262E-4,6.224437489477729E-4,6.570257872898878E-4,6.897854345653862E-4,7.198992453650314E-4,7.470702010947003E-4,7.719902644628787E-4,7.953707899618223E-4,8.189219479950767E-4,8.429988553311521E-4,8.672511954838461E-4,8.920786288472599E-4,9.184339757718049E-4,9.477296298926281E-4,9.79612602305429E-4,0.0010140072486055896,0.0010529857154862852,0.0010985163655867162,0.0011512181616172242,0.0012122168844045252,0.0012817962747987922,0.001359918417094126,0.0014442577891093354,0.0015315582094212828,0.0016186474157646679,0.001703910240098424,0.001784901938282465,0.001859407230833659,0.0019258190573811218,0.00198310463344881,0.0020290942052996726,0.0020621573167113757,0.0020812326646715163,0.0020858253599325104,0.0020777540802606282,0.0020583345011823415,0.0020298779045752687,0.0019947586814735366,0.0019539471021681487,0.0019095287801248954,0.0018639906620815665,0.0018190441797413406,0.0017773193591413667,0.001740197062584523,0.0017110507170960624,0.0016921758016617899,0.0016845623269758452,0.0016894367070003366,0.001706416030993837,0.0017363448633489953,0.0017787815462471396,0.001830654333659411,0.001889440224195671,0.00195212

In [12]:
df.densityPlot("depth")

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="gKSilV"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density"
},
"stat":"identity",
"data":{
"density":[4.4745487622806146E-5,4.696816529975255E-5,4.9233293830303676E-5,5.153731555102641E-5,5.387633276816177E-5,5.624611129478038E-5,5.864209041236017E-5,6.105939982177893E-5,6.349288396567802E-5,6.593713389500998E-5,6.838652662506085E-5,7.083527168925842E-5,7.327746436241661E-5,7.570714479888997E-5,7.811836212549253E-5,8.050524235343432E-5,8.286205883632316E-5,8.518330390927977E-5,8.746376030227882E-5,8.969857093154006E-5,9.188330573629249E-5,9.401402434205878E-5,9.608733349085005E-5,9.810043837604224E-5,1.00051187245957E-4,1.0193810888445897E-4,1.0376044282723836E-4,1.0551816241653399E-4,1.0721199102260851E-4,1.0884341195590564E-4,1.1041467274953226E-4,1.1192878459951065E-4,1.1338951780461206E-4,1.1480139404582086E-4,1.1616967628787538E-4,1.1750035697532572E-4,1.1880014503949158E-4,1.2007645203972864E-4,1.213373775439211E-4,1.2259169362225652E-4,1.2384882809946094E-4,1.2511884599835198E-4,1.2641242842620088E-4,1.2774084801807153E-4,1.2911593996937963E-4,1.305500676721586E-4,1.3205608202175126E-4,1.3364727358514844E-4,1.3533731701773308E-4,1.3714020737666795E-4,1.3907018829802356E-4,1.4114167236907113E-4,1.4336915442223874E-4,1.4576711888616745E-4,1.4834994273368746E-4,1.5113179594735402E-4,1.5412654176153617E-4,1.5734763921820846E-4,1.6080805077558423E-4,1.6452015782133876E-4,1.6849568695538134E-4,1.7274564981478152E-4,1.7728029901348678E-4,1.821091024641407E-4,1.8724073794515873E-4,1.9268310928388516E-4,1.9844338496041402E-4,2.0452805931399834E-4,2.1094303587480825E-4,2.1769373166968087E-4,2.2478520068392014E-4,2.3222227402433531E-4,2.4000971374304837E-4,2.4815237676644E-4,2.5665538494609236E-4,2.6552429692217115E-4,2.7476527727442527E-4,2.8438525833768535E-4,2.943920900790142E-4,3.0479467356997415E-4,3.1560307383331736E-4,3.268286081887827E-4,3.3848390665449794E-4,3.5058294146366766E-4,3.6314102331389035E-4,3.7617476256143994E-4,3.8970199418804596E-4,4.0374166598730827E-4,4.183136900276523E-4,4.334387580374131E-4,4.491381219162523E-4,4.654333411006914E-4,4.8234599899770007E-4,4.99897391150355E-4,5.181081882170567E-4,5.36998077237055E-4,5.565853850268467E-4,5.768866879127005E-4,5.979164123608389E-4,6.196864314246854E-4,6.422056622908286E-4,6.65479670571771E-4,6.895102873594503E-4,7.142952454096919E-4,7.398278411604051E-4,7.660966295763934E-4,7.930851590385885E-4,8.207717536288285E-4,8.49129350174689E-4,8.781253972829936E-4,9.077218232774836E-4,9.378750794400418E-4,9.685362642152697E-4,9.996513330608216E-4,0.0010311613974048957,0.00106300311471148,0.0010951091699676631,0.0011274088470219288,0.0011598286861550066,0.0011922932221040702,0.0012247257945453543,0.0012570494208360408,0.0012891877186964123,0.0013210658645537916,0.00135261157154707,0.0013837560697783538,0.0014144350703638093,0.0014445896942369915,0.0014741673465403324,0.0015031225178347132,0.0015314174942760964,0.0015590229603474825,0.0015859184796696373,0.0016120928418024679,0.0016375442657296426,0.0016622804538162866,0.001686318493353416,0.001709684606253592,0.001732413750935259,0.001754549083820206,0.0017761412910652266,0.0017972478040555238,0.001817931914717397,0.0018382618087848725,0.0018583095367235754,0.0018781499430355448,0.0018978595751227485,0.0019175155927767251,0.0019371946987085911,0.0019569721093776306,0.0019769205837737807,0.0019971095258286475,0.0020176041738501384,0.0020384648878806807,0.002059746543257072,0.0020814980359830

In case you want to provide input and weights using column selection DSL,
it's a bit different from the usual one — you should assign `x`
input and (optionally) `weight` throw invocation eponymous functions:

In [13]:
df.densityPlot(adjust = 0.5) {
    x(depth)
    weight(coeff)
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="SfgXsj"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"depth",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"densityWeighted"
},
"stat":"identity",
"data":{
"x":[185.72529353296983,187.01309958779512,188.30090564262045,189.58871169744575,190.87651775227107,192.16432380709637,193.4521298619217,194.739935916747,196.0277419715723,197.3155480263976,198.60335408122293,199.89116013604823,201.17896619087355,202.46677224569885,203.75457830052414,205.04238435534947,206.3301904101748,207.6179964650001,208.9058025198254,210.1936085746507,211.481414629476,212.76922068430133,214.05702673912663,215.34483279395195,216.63263884877725,217.92044490360257,219.20825095842787,220.4960570132532,221.7838630680785,223.0716691229038,224.3594751777291,225.6472812325544,226.93508728737973,228.22289334220505,229.51069939703035,230.79850545185565,232.08631150668097,233.37411756150627,234.6619236163316,235.9497296711569,237.2375357259822,238.5253417808075,239.81314783563283,241.10095389045813,242.38875994528343,243.67656600010875,244.96437205493407,246.25217810975937,247.53998416458467,248.82779021941,250.11559627423532,251.4034023290606,252.6912083838859,253.97901443871123,255.26682049353656,256.55462654836185,257.84243260318715,259.13023865801244,260.41804471283774,261.7058507676631,262.9936568224884,264.2814628773137,265.56926893213904,266.85707498696434,268.14488104178963,269.4326870966149,270.7204931514402,272.0082992062656,273.2961052610909,274.58391131591617,275.8717173707415,277.1595234255668,278.4473294803921,279.7351355352174,281.0229415900427,282.310747644868,283.59855369969335,284.88635975451865,286.17416580934395,287.4619718641693,288.7497779189946,290.0375839738199,291.3253900286452,292.6131960834705,293.90100213829584,295.18880819312113,296.47661424794643,297.7644203027718,299.0522263575971,300.3400324124224,301.62783846724767,302.91564452207297,304.20345057689826,305.4912566317236,306.7790626865489,308.0668687413742,309.35467479619956,310.64248085102486,311.93028690585015,313.21809296067545,314.50589901550075,315.79370507032604,317.0815111251514,318.3693171799767,319.65712323480204,320.94492928962734,322.23273534445264,323.52054139927793,324.8083474541032,326.0961535089285,327.3839595637539,328.6717656185792,329.95957167340447,331.2473777282298,332.5351837830551,333.8229898378804,335.1107958927057,336.398601947531,337.6864080023563,338.97421405718165,340.26202011200695,341.5498261668323,342.8376322216576,344.1254382764829,345.4132443313082,346.7010503861335,347.9888564409588,349.27666249578414,350.56446855060943,351.85227460543473,353.1400806602601,354.4278867150854,355.7156927699107,357.00349882473597,358.29130487956127,359.57911093438656,360.8669169892119,362.1547230440372,363.44252909886256,364.73033515368786,366.01814120851316,367.30594726333845,368.59375331816375,369.88155937298905,371.1693654278144,372.4571714826397,373.744977537465,375.03278359229034,376.32058964711564,377.60839570194094,378.89620175676623,380.1840078115915,381.4718138664168,382.7596199212422,384.0474259760675,385.3352320308928,386.6230380857181,387.9108441405434,389.1986501953687,390.486456250194,391.7742623050193,393.0620683598446,394.34987441466996,395.63768046949525,396.9254865243206,398.2132925791459,399.5010986339712,400.7889046887965,402.0767107436218,403.3645167984471,404.65232285327244,405.94012890809773,407.2279349629231,408.5157410177484,409.8035470725737,411.091353127399,412.37915918222427,413.66696523704957,414.95477129187486,416.2425773467002,417.5303834015255,418.81818945635086,

`densityPlot` plot can be configured with `.configure {}` extension — it opens context that combines area,
`StatDensity` and plot context.
That means you can configure bars settings, mappings using `StatDensity` dataset and any plot adjustments:

In [14]:
df.densityPlot {
    x(depth)
}.configure {
    // Area + StatDensity + PlotContext
    // Can't add new layer
    // Can add area mapping, including for `Stat.*` columns
    fillColor(Stat.scaled) // doesn't work properly for now
    alpha = 0.6
    // Can configure general plot adjustments
    layout {
        title = "Configured `densityPlot` plot"
        size = 600 to 350
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="9sXily"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"ggtitle":{
"text":"Configured `densityPlot` plot"
},
"mapping":{
},
"data":{
"density":[4.4745487622806146E-5,4.696816529975255E-5,4.9233293830303676E-5,5.153731555102641E-5,5.387633276816177E-5,5.624611129478038E-5,5.864209041236017E-5,6.105939982177893E-5,6.349288396567802E-5,6.593713389500998E-5,6.838652662506085E-5,7.083527168925842E-5,7.327746436241661E-5,7.570714479888997E-5,7.811836212549253E-5,8.050524235343432E-5,8.286205883632316E-5,8.518330390927977E-5,8.746376030227882E-5,8.969857093154006E-5,9.188330573629249E-5,9.401402434205878E-5,9.608733349085005E-5,9.810043837604224E-5,1.00051187245957E-4,1.0193810888445897E-4,1.0376044282723836E-4,1.0551816241653399E-4,1.0721199102260851E-4,1.0884341195590564E-4,1.1041467274953226E-4,1.1192878459951065E-4,1.1338951780461206E-4,1.1480139404582086E-4,1.1616967628787538E-4,1.1750035697532572E-4,1.1880014503949158E-4,1.2007645203972864E-4,1.213373775439211E-4,1.2259169362225652E-4,1.2384882809946094E-4,1.2511884599835198E-4,1.2641242842620088E-4,1.2774084801807153E-4,1.2911593996937963E-4,1.305500676721586E-4,1.3205608202175126E-4,1.3364727358514844E-4,1.3533731701773308E-4,1.3714020737666795E-4,1.3907018829802356E-4,1.4114167236907113E-4,1.4336915442223874E-4,1.4576711888616745E-4,1.4834994273368746E-4,1.5113179594735402E-4,1.5412654176153617E-4,1.5734763921820846E-4,1.6080805077558423E-4,1.6452015782133876E-4,1.6849568695538134E-4,1.7274564981478152E-4,1.7728029901348678E-4,1.821091024641407E-4,1.8724073794515873E-4,1.9268310928388516E-4,1.9844338496041402E-4,2.0452805931399834E-4,2.1094303587480825E-4,2.1769373166968087E-4,2.2478520068392014E-4,2.3222227402433531E-4,2.4000971374304837E-4,2.4815237676644E-4,2.5665538494609236E-4,2.6552429692217115E-4,2.7476527727442527E-4,2.8438525833768535E-4,2.943920900790142E-4,3.0479467356997415E-4,3.1560307383331736E-4,3.268286081887827E-4,3.3848390665449794E-4,3.5058294146366766E-4,3.6314102331389035E-4,3.7617476256143994E-4,3.8970199418804596E-4,4.0374166598730827E-4,4.183136900276523E-4,4.334387580374131E-4,4.491381219162523E-4,4.654333411006914E-4,4.8234599899770007E-4,4.99897391150355E-4,5.181081882170567E-4,5.36998077237055E-4,5.565853850268467E-4,5.768866879127005E-4,5.979164123608389E-4,6.196864314246854E-4,6.422056622908286E-4,6.65479670571771E-4,6.895102873594503E-4,7.142952454096919E-4,7.398278411604051E-4,7.660966295763934E-4,7.930851590385885E-4,8.207717536288285E-4,8.49129350174689E-4,8.781253972829936E-4,9.077218232774836E-4,9.378750794400418E-4,9.685362642152697E-4,9.996513330608216E-4,0.0010311613974048957,0.00106300311471148,0.0010951091699676631,0.0011274088470219288,0.0011598286861550066,0.0011922932221040702,0.0012247257945453543,0.0012570494208360408,0.0012891877186964123,0.0013210658645537916,0.00135261157154707,0.0013837560697783538,0.0014144350703638093,0.0014445896942369915,0.0014741673465403324,0.0015031225178347132,0.0015314174942760964,0.0015590229603474825,0.0015859184796696373,0.0016120928418024679,0.0016375442657296426,0.0016622804538162866,0.001686318493353416,0.001709684606253592,0.001732413750935259,0.001754549083820206,0.0017761412910652266,0.0017972478040555238,0.001817931914717397,0.0018382618087848725,0.0018583095367235754,0.0018781499430355448,0.0018978595751227485,0.0019175155927767251,0.0019371946987085911,0.0019569721093776306,0.0019769205837737807,0.0019971095258286475,0.0020176041738501384,0.0020384648878806807,0.002059746543257072,0.0020814980359830973,0.002103761902895912,0.0021265740570835107,0.002149963636654558,0.0021739529628209057,0.0021985576013628457,0.0022237865199288614,0.002249642332284175,0.00227612161956413,0.002303215317797583,

## Grouped `statDensity`

`statDensity` can be applied for grouped data —
statistics will be calculated on each group independently but with equal categories.
This application returns a new `GroupBy`
dataset with the same keys as the old one but with `StatDensity` groups instead of old ones.

In [15]:
// Create two samples from normal distribution with different mean/std
val rangesA = NormalDistribution(500.0, 100.0).sample(5000).toList()
val rangesB = NormalDistribution(400.0, 80.0).sample(5000).toList()

// Gather them into `DataFrame` with "A" and "B" keys in the "category" column
val rangesDF = dataFrameOf(
    "range" to rangesA + rangesB,
    "category" to List(5000) { "A" } + List(5000) { "B" }
)
rangesDF.head()

<iframe onload="o_resize_iframe_out_3()" style="width:100%;" class="result_container" id="iframe_out_3" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-687865854"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for 

It has the following signature:

| range | category |
|-------|----------|

In [16]:
// Group it by "category"
val groupedRangesDF = rangesDF.groupBy { category }
groupedRangesDF

<iframe onload="o_resize_iframe_out_4()" style="width:100%;" class="result_container" id="iframe_out_4" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-687865853"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.length; i++

Now we have a `GroupBy` with a signature

<table>
  <thead>
    <tr>
      <th>key: [category]</th>
      <th>group: DataFrame[range|category]</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>A</td>
      <td>A-Group</td>
    </tr>
    <tr>
      <td>B</td>
      <td>B-Group</td>
    </tr>
  </tbody>
</table>

In [17]:
groupedRangesDF.statDensity { x(range) }

<iframe onload="o_resize_iframe_out_5()" style="width:100%;" class="result_container" id="iframe_out_5" frameBorder="0" srcdoc=" <html theme='dark'>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-687865850"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.length; i++

After `statDensity` applying it's still a `GroupBy` but with different signature of `group` -
all groups have the same signature as usual `DataFrame` after `statDensity` applying (i.e. `StatDensityFrame`):

<table>
  <thead>
    <tr>
      <th>key: [drv]</th>
      <th>group: StaDensityFrame</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>"A"</td>
      <td>"A"-Group</td>
    </tr>
    <tr>
      <td>"B"</td>
      <td>"B"-Group</td>
    </tr>
  </tbody>
</table>

As you can see, we did indeed do a `statDensity` transformation within groups, the grouping keys did not change.
The plotting process doesn't change much — we do everything the same.

In [18]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
        }
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="lN972r"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B

As you can see, there are two lines because we have two groups of data.
To distinguish them, we need to add mapping to the color from the key.
This is convenient — the key is available in the context

In [19]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
            color(key.category)
        }
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="o7hJ45"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","

The `densityPlot()` layer also works.
Moreover, if we have exactly one grouping key, a mapping from it to `fillColor`
and `borderLine.color` will be created by default.

In [20]:
groupedRangesDF.plot {
    densityPlot(range)
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="Len1Tf"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

We can customize it like we used to. From the differences — access to `key` columns:

In [21]:
groupedRangesDF.plot {
    densityPlot(range) {
        // Customize scale of default mapping
        fillColor(key.category) {
            scale = categorical("A" to Color.GREEN, "B" to Color.ORANGE)
        }
        borderLine.color = Color.BLACK
        alpha = 0.5
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="4N36xf"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"values":["#3ba272","#fc8452"],
"limits":["A","B"]
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","

Also, we can stack areas (for that we need `x` coordinates to match — use `trim = true`):

In [22]:
groupedRangesDF.plot {
    // Use trim
    densityPlot(range, trim = true) {
        // Adjust position of areas from different groups
        position = Position.stack()
        alpha = 0.8
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="rfUK5G"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

`densityPlot` plot for `GroupBy` (i.e. `GroupBy.densityPlot(statDensityArgs)` extensions) works as well:

In [23]:
groupedRangesDF.densityPlot("range", bandWidth = BandWidth.value(10.0))

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="aQP3i4"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

... and can be configured the same way:

In [24]:
groupedRangesDF.densityPlot(n = 750, trim = true, adjust = 0.75) { x(range) }.configure {
    alpha = 0.6
    position = Position.stack()
    // Can access key column by name as `String`
    fillColor("category") { scale = categoricalColorBrewer(BrewerPalette.Qualitative.Dark2) }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="qFE3Y8"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",

### Inside `groupBy{}` plot context

We can apply `groupBy` modification to the initial dataset and build a density plot with grouped data the same way:

In [25]:
rangesDF.plot {
    groupBy(category) {
        densityPlot(range)
    }
}

<head>
 <style> html, body { margin: 0; overflow: hidden; } </style>
 <script type="text/javascript" data-lets-plot-script="library" src="https://cdn.jsdelivr.net/gh/JetBrains/lets-plot@v4.0.1/js-package/distr/lets-plot.min.js"></script>
 </head>
 <body>
 <div id="0c8O6j"></div>
 <script type="text/javascript" data-lets-plot-script="plot">
 var plotSpec={
"mapping":{
},
"data":{
},
"kind":"plot",
"scales":[{
"aesthetic":"x",
"name":"range",
"limits":[null,null]
},{
"aesthetic":"x",
"limits":[null,null]
},{
"aesthetic":"y",
"limits":[null,null]
},{
"aesthetic":"fill",
"discrete":true
},{
"aesthetic":"color",
"discrete":true
}],
"layers":[{
"mapping":{
"x":"x",
"y":"density",
"fill":"category",
"color":"category",
"group":"&merged_groups"
},
"stat":"identity",
"data":{
"&merged_groups":["A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","A","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B","B",